# Sujet 5 : Analyse des dialogues dans l'Avare de Molière

__Rappel du contexte du sujet__ :

L’Observatoire de la vie littéraire ([OBVIL](http://obvil.sorbonne-universite.site/obvil/presentation)) promeut une approche de l'analyse des textes littéraires fondée sur le numérique. 
Dans le cadre du [Projet Molière](http://obvil.sorbonne-universite.site/projets/projet-moliere), des pièces de cet auteur ont été numérisées et sont accessibles librement dans différents formats utilisables par un programme informatique.  

Grâce à ces numérisations, il est possible d'écrire des programmes pour réaliser des analyses syntaxiques et sémantiques. Ce sujet se propose de reproduire une étude réalisée par l'OBVIL sur les dialogues de l'Avare de Molière.

__Rappel des objectifs de ce sujet__ :

1. Classez les personnages selon la quantité de parole grâce à une analyse syntaxique du texte (scènes / répliques / mots). En particulier, quel est celui qui parle le plus ? Quel est celui qui ne parle pas du tout ? Attention, les noms des personnages ne sont pas forcément homogènes (casse et accents par exemple).
2. Réalisez un graphique qui montrera le nombre de mots que chaque acteur prononce dans chaque scène. Pour cela, vous pouvez vous inspirer de l'[étude de l'Avare de Molière réalisée par l'OBVIL](https://obvil.sorbonne-universite.fr/corpus/moliere/moliere_avare) (graphe de gauche). Dans ce graphique, les lignes sont de longueur égale et la hauteur représente le nombre de mots prononcés au total dans la scène. La largeur de chaque rectangle indique le pourcentage de la scène qu’un acteur occupe.  
3. Facultatif : Construisez un graphe d’interlocution permettant de visualiser les échanges entre les personnages. Pour cela, vous pouvez vous inspirer de l'[étude de l'Avare de Molière réalisée par l'OBVIL](https://obvil.sorbonne-universite.fr/corpus/moliere/moliere_avare) (graphe de droite).
4. Déposer votre résultat dans FUN

La version numérisée que l'on se propose d'utiliser est le fichier texte au format markdown disponible ici [moliere_avare](http://dramacode.github.io/markdown/moliere_avare.txt).

In [1]:
data_url = "http://dramacode.github.io/markdown/moliere_avare.txt"

On va s'assurer qu'un fichier texte en local au format markdown contienne la pièce. Si le fichier "moliere_avare.md" existe on considère que c'est bon et s'il n'existe pas nous allons télécharger le contenu disponible à l'URL renseignée ci-dessus et l'écrire dans ce fichier local "moliere_avare.md".  

In [ ]:
# from os import path as pth
import requests

local_filename = "moliere_avare.md"
# Si le fichier csv des données d'incidence existe en local
# il n'est pas nécessaire de le télécharger par l'URL
if not pth.exists(local_filename):
  # Si le fichier n'existe pas en local dans le dossier courant
  # nous téléchargons les données et les écrivons
  # dans un fichier en local
  # Téléchargement des données
  response = requests.get(data_url)
  # Ecriture des données téléchargées dans le fichier local
  with open(local_filename, "wb") as f:
    f.write(response.content)

Maintenant que nous sommes assurés d'avoir un fichier en local contenant le texte de l'Avare dont on va faire l'analyse, on va donc l'ouvrir, parcourir son contenu et le traiter au fur et à mesure.

Ce que l'on sait déjà c'est que l'on va devoir créer une structure de données pour l'analyse.
On va passer par la bibliothèque Pandas et la création d'un dataframe, permettant de différencier les différents personnages et de qualifier leur "activité" au travers des différents actes et scènes. Néanmoins, après avoir parcouru le web, il est recommandé de passer par une structure intermédiaire pour la création du dataframe pandas. Nous allons choisir la structure de données native de python des dictionnaires en tant que structure de données intermédiaire. 

Il y a plusieurs choses auxquelles il est déjà nécessaire de penser vis-à-vis de la problématique posée et des représentations graphiques demandées, notamment celle relative à la question facultative.

Pour commencer, afin d'obtenir une bonne lisibilité des graphiques, il sera intéressant d'associer à chaque personnage une couleur différente.

Ensuite, la question facultative demande de déterminer à qui s'adresse chaque réplique afin d'avoir le graphe directionnel des interactions entre les personnages de la pièce. La structure de données devra donc permettre de savoir pour chaque réplique l'auteur mais aussi le destinataire de cette dernière. Ce sont des informations assez simples à obtenir mais à prendre en compte dans la manière de "parser" le fichier texte.

In [3]:
# On va d'ores et déjà utiliser une instruction afin que les graphiques s'affichent directement au sein du notebook
%matplotlib inline

In [7]:
# On déclare l'utilisation de la bibliothèque pandas et on crée également le dictionnaire
# qui va nous servir d'intermédiaire avant la création du dataframe pandas
import pandas as pd
# Le dictionnaire établi une structure en tableau à 5 colonnes permettant d'enregistrer
# l'auteur, le destinataire, l'acte, la scène, ainsi que la longueur en termes de mots 
# pour chaque réplique de la pièce
avareAnalysisDict = {'author':[],'recipient':[],'act':[],'scene':[],'speech_lenght':[]}

# Nous créons également d'ores et déjà un dictionnaire des personnages de la scène
# permettant d'enregistrer les informations de liens avec les autres personnages
# de définir une couleur de représentation.

# Ce dictionnaire est initialisé vide car il sera rempli en utilisant le nom de chaque personnage
# comme clés associées à des valeurs qui seront des dictionnaires à deux entrées
# 'links' donnant les liens avec les autres personnages sous la forme d'une liste
# 'color' permettant de régler une couleur de représentation
avarePersoDict = {}

Afin de parser le fichier en s'appuyant notamment sur les symboles de titres utilisés par le format Markdown,
il nous faut avoir recours à l'utilisation d'un outil d'analyse des expressions régulières (cf. [Wikipedia_Expression_régulière](https://fr.wikipedia.org/wiki/Expression_r%C3%A9guli%C3%A8re)). La bibliothèque
[re](https://docs.python.org/3/library/re.html) disponible nativement dans python permet de faire ce travail. 

In [9]:
import re

In [28]:
# Chaîne de caractère indiquant le début d'analyse et de récupération des personnages
persoCaptureSTartLine = "# ACTEURS."
# L'expression régulière suivante permet de valider qu'une chaîne de caractère
# contenue dans une ligne lue correspond à la ligne précédant la définition
# de la liste des personnages
m = re.search('(?<=# )ACTEURS\.$', persoCaptureSTartLine)
m.group(0)

'ACTEURS.'

En effet, le résultats obtenus n'est pas un objet null, valeur None python

In [47]:
# Exemple d'une ligne de la liste des personnages
persoLineExample = " – Harpagon, Père de Cléante et d'Élise, et Amoureux de Mariane."
# L'expression régulière proposée est la suivante
# On cherche une chaîne de caractères Commencant par une majuscule --> [A-ZÀ-Ÿ]{1}
# potentiellement accentuée et ensuite composées de lettres potentiellement
# accentuées elles aussi, contenant des espaces, des virgules, des apostrophes --> [a-zA-ZÀ-ÿ\s,\']+
# et précédée d'un espace suivi d'un tiret suivi d'un espace (ce n'est pas le tiret du 6) --> (?<=\s–\s)
m1 = re.search('(?<=\s–\s)[A-ZÀ-Ÿ]{1}[a-zA-ZÀ-ÿ\s,\']+',persoLineExample)
m1.group(0)

"Harpagon, Père de Cléante et d'Élise, et Amoureux de Mariane"

Voici un lien vers un site de test en ligne d'expressions régulières python \([regexp_test](https://pythex.org/)\) qui a aidé à mettre en place l'expression régulière précédente.

In [8]:
def fill_perso_dict(fileToAnalyse, emptyPersoDict):
  currentLine = fileToAnalyse.readline()
  isStartPersoListLine = False
  while (currentLine and not isStartPersoListLine):
    m = re.search('(?<=# )ACTEURS\.$', currentLine)
    if m is not None:
      isStartPersoListLine = True
    currentLine = fileToAnalyse.readline()
    
  # La lecture s'est arrêtée car la ligne de début de définition
  # de la liste des personnages a été rencontrée.
  # Nous avons néanmoins lue la ligne suivante.
  # Nous devons maintenant lire ligne par ligne,
  # la liste des personnages au format suivant:
  # "- NomPersonnage, lien, lien, ..."
  # Ainsi dès que la ligne ne commence plus par un tiret
  # nous pouvons arrêter la lecture et le remplissage
  # du dictionnaire.
  

{'author': [], 'recipient': [], 'act': [], 'scene': [], 'speech_lenght': []}

In [ ]:
# On ouvre le fichier local en lecture 'r' pour en faire l'analyse
# en utilisant l'instruction with qui se chargera de fermer
# le fichier une fois sortie de l'instruction.
# (pas d'erreur possible par oubli d'appel à l'instruction close)
# Un rapide coup d'oeil au fichier texte nous montre une organisation
# , des symboles en début de ligne etc, que l'on va utiliser pour "parser"
# le fichier, à savoir le lire de manière à ranger les données
# de manière intelligente dans une structure de données facilitant
# la manipulation et l'analyse. 
with open(local_filename,'r') as avare_file:
  # On va commencer par parser le fichier afin de définir des couleurs pour chaque personnage
  pass

Notes pour plus tard: lien stack overflow vers code de customisation de graphes de la bibliothèque python networkx
https://stackoverflow.com/questions/25639169/networkx-change-color-width-according-to-edge-attributes-inconsistent-result
lien github vers morceau de code ajoutant de la couleur et le réglage de l'épaisseur des arêtes sur un graphe
https://gist.github.com/AruniRC/2c53fe7680eeb578593ec816bbfb1653
Lien vers une page donnant un exemple d'affichage par ensemble de barres
https://www.geeksforgeeks.org/stacked-percentage-bar-plot-in-matplotlib/